# Interactive Data Science Final Project
Team 25: TheVizKids

## Data Processing and Machine Learning
#### **Motivation:**
As stated, missing Energy Score Values pose a problem to the dashboard. Since this metric cannot be computed given the data available, Machine Learning approaches are used to estimate this value for missing cases.

Taking a brute force approach of assigning a mean calculated by clustering similar building types yeilds an unnformative value (often 50) as even within a building type, the values range from [1,100]. Thus ML is essential in solving this problem.

#### **Formulating the problem as an ML Problem:**
The problem at hand can be seen as a regression problem since the Energy Star Score is a continuous value between 1 and 100. It can be seen a regression over the following features from our dataset. The following consitutues our feature set or X
- Year built
- Number of floors
- Area of the Property
- Type of Property
- Source Energy Use Intensity (EUI)
- GHG Emission

Energy Star Score serves as our labels or Y.

#### **Procedure:**
Some features from the above list of X have missing values. These have been removed to help the model attain better accuracy.

All the columns except the Type of Property are numeric in nature and can be used directly. In order to encode the relationship between two buildings types in the representation fed to the model, we obtain their BERT Encoding. For example, 'Multifamily Housing' and 'Residence Hall' are more similar than  'Multifamily Housing' and 'Hospital'. Thus we cleaned the Property Type column and encoded it using BERT.

Finally, we concatenate the columns for X along with the BERT encoding and feed it to our model.

70-30 train-test split has been used. Subsequently, cross validation is done on the 70% or train dataset to verify results. Finally the results are reported on the test dataset.

The models we experimented with are
1. K Nearest Neighbors
1. K Means
1. Linear Regression
1. Support Vector Regressor
1. Decision Tree
1. Random Forest
1. Ridge Regressor
1. Multi Layer Perceptron

Out of which, Random Forests attain the best performance of 67.1% average accuracy on 5 fold cross validation and 68.7% on test set so far.


#### Future Work:
- Explore different flavour of BERT for the encoding
- Try dimensionality reduction - PCA or SVD
- Feature Engineering to modify year build to age of the building etc



In [ ]:
! pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip 

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     - 22.0 MB 137 kB/s
     |████████████████████████████████| 102 kB 26.6 MB/s 
     |████████████████████████████████| 690 kB 40.0 MB/s 
     |████████████████████████████████| 62 kB 1.8 MB/s 
     |████████████████████████████████| 9.9 MB 73.2 MB/s 
     |████████████████████████████████| 4.7 MB 59.7 MB/s 
     |████████████████████████████████| 296 kB 90.9 MB/s 
  Created wheel for pandas-profiling: filename=pandas_profiling-3.4.0-py2.py3-none-any.whl size=315268 sha256=85f987fb5db62247d161f5fb7c38cc8be0b837af1ceccd7bff1793c634b07ce8
  Stored in directory: /tmp/pip-ephem-wheel-cache-q6re906x/wheels/cc/d5/09/083fb07c9363a2f45854b0e3a7de7d7c560f07da74b9e9769d
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27098 sha256=bc6d355a7d0b16680c2a35efe9750d9b4af0f34cfc389cac8ec0b57411b219e1
  Stored in directory: /root/.cache/pip/wheels/70/e1/52/5b14d250ba86876882394

In [1]:
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport

In [ ]:
df = pd.read_csv('/content/drive/MyDrive/05839_Final Project/Data/Final dataset/Individual Building Data/Combined.csv')
# df.head()

In [ ]:
profile = ProfileReport(df)

In [ ]:
profile.to_notebook_iframe()

In [ ]:
idx = [x for x in range(len(df)) if x not in np.where(df['ENERGYSTARScore'].isna())[0]]
df_energystar = df.iloc[idx]
len(df_energystar)

10181

In [ ]:
df_energystar.head()

OSEBuildingID  DataYear PrimaryPropertyType          Address     City  \
0              1      2016               Hotel    405 Olive way  Seattle   
1              2      2016               Hotel  724 Pine street  Seattle   
2              3      2016               Hotel  1900 5th Avenue  Seattle   
3              5      2016               Hotel   620 STEWART ST  Seattle   
4              8      2016               Hotel    401 LENORA ST  Seattle   

  State  ZipCode TaxParcelIdentificationNumber Neighborhood  Latitude  ...  \
0    WA  98101.0                    0659000030     DOWNTOWN  47.61220  ...   
1    WA  98101.0                    0659000220     DOWNTOWN  47.61317  ...   
2    WA  98101.0                    0659000475     DOWNTOWN  47.61393  ...   
3    WA  98101.0                    0659000640     DOWNTOWN  47.61412  ...   
4    WA  98121.0                    0659000970     DOWNTOWN  47.61375  ...   

   SiteEUIWN(kBtu/sf)  SourceEUIWN(kBtu/sf)  SiteEnergyUseWN(kBtu)  \
0           84.300003            189.000000              7456910.0   
1           97.900002            179.399994              8664479.0   
2           97.699997            244.100006             73937112.0   
3          113.300003            224.000000              6946800.5   
4          118.699997            215.600006             14656503.0   

   SteamUse(kBtu)  Electricity(kBtu)  NaturalGas(kBtu)  DefaultData  \
0      2003882.00          3946027.0         1276453.0        False   
1            0.00          3242851.0         5145082.0        False   
2     21566554.00         49526664.0         1493800.0        False   
3      2214446.25          2768924.0         1811213.0        False   
4            0.00          5368607.0         8803998.0        False   

  ComplianceStatus Outlier  GHGEmissionsIntensity  
0        Compliant     NaN                   2.83  
1        Compliant     NaN                   2.86  
2        Compliant     NaN                   2.19  
3        Compliant     NaN                   4.67  
4        Compliant     NaN                   2.88  

[5 rows x 35 columns]

In [ ]:
df_energystar.to_csv('/content/drive/MyDrive/05839_Final Project/Data/Final dataset/Individual Building Data/dataForML.csv', index=False)

## Picking the columns

In [10]:
df_energystar = pd.read_csv('/content/drive/MyDrive/05839_Final Project/Data/Final dataset/Individual Building Data/dataForML.csv')
df_energystar.head()

OSEBuildingID  DataYear PrimaryPropertyType          Address     City  \
0              1      2016               Hotel    405 Olive way  Seattle   
1              2      2016               Hotel  724 Pine street  Seattle   
2              3      2016               Hotel  1900 5th Avenue  Seattle   
3              5      2016               Hotel   620 STEWART ST  Seattle   
4              8      2016               Hotel    401 LENORA ST  Seattle   

  State  ZipCode TaxParcelIdentificationNumber Neighborhood  Latitude  ...  \
0    WA  98101.0                    0659000030     DOWNTOWN  47.61220  ...   
1    WA  98101.0                    0659000220     DOWNTOWN  47.61317  ...   
2    WA  98101.0                    0659000475     DOWNTOWN  47.61393  ...   
3    WA  98101.0                    0659000640     DOWNTOWN  47.61412  ...   
4    WA  98121.0                    0659000970     DOWNTOWN  47.61375  ...   

   SiteEUIWN(kBtu/sf)  SourceEUIWN(kBtu/sf)  SiteEnergyUseWN(kBtu)  \
0           84.300003            189.000000              7456910.0   
1           97.900002            179.399994              8664479.0   
2           97.699997            244.100006             73937112.0   
3          113.300003            224.000000              6946800.5   
4          118.699997            215.600006             14656503.0   

   SteamUse(kBtu)  Electricity(kBtu)  NaturalGas(kBtu)  DefaultData  \
0      2003882.00          3946027.0         1276453.0        False   
1            0.00          3242851.0         5145082.0        False   
2     21566554.00         49526664.0         1493800.0        False   
3      2214446.25          2768924.0         1811213.0        False   
4            0.00          5368607.0         8803998.0        False   

  ComplianceStatus Outlier  GHGEmissionsIntensity  
0        Compliant     NaN                   2.83  
1        Compliant     NaN                   2.86  
2        Compliant     NaN                   2.19  
3        Compliant     NaN                   4.67  
4        Compliant     NaN                   2.88  

[5 rows x 35 columns]

In [11]:
df_energystar.columns

Index(['OSEBuildingID', 'DataYear', 'PrimaryPropertyType', 'Address', 'City',
       'State', 'ZipCode', 'TaxParcelIdentificationNumber', 'Neighborhood',
       'Latitude', 'Longitude', 'YearBuilt', 'NumberofBuildings',
       'NumberofFloors', 'PropertyGFATotal', 'PropertyGFAParking',
       'PropertyGFABuilding(s)', 'ListOfAllPropertyUseTypes',
       'LargestPropertyUseType', 'LargestPropertyUseTypeGFA',
       'SecondLargestPropertyUseType', 'SecondLargestPropertyUseTypeGFA',
       'ThirdLargestPropertyUseType', 'ThirdLargestPropertyUseTypeGFA',
       'ENERGYSTARScore', 'SiteEUIWN(kBtu/sf)', 'SourceEUIWN(kBtu/sf)',
       'SiteEnergyUseWN(kBtu)', 'SteamUse(kBtu)', 'Electricity(kBtu)',
       'NaturalGas(kBtu)', 'DefaultData', 'ComplianceStatus', 'Outlier',
       'GHGEmissionsIntensity'],
      dtype='object')

In [14]:
columns = [
    'YearBuilt',
    'NumberofFloors',
    'PropertyGFABuilding(s)',
    'LargestPropertyUseType',
    'ENERGYSTARScore', 
    'SourceEUIWN(kBtu/sf)',
    'SiteEUIWN(kBtu/sf)',
    'GHGEmissionsIntensity'
]

df_energystar = df_energystar[columns]
df_energystar.columns

Index(['YearBuilt', 'NumberofFloors', 'PropertyGFABuilding(s)',
       'LargestPropertyUseType', 'ENERGYSTARScore', 'SourceEUIWN(kBtu/sf)',
       'SiteEUIWN(kBtu/sf)', 'GHGEmissionsIntensity'],
      dtype='object')

In [15]:
df_energystar.describe()

YearBuilt  NumberofFloors  PropertyGFABuilding(s)  ENERGYSTARScore  \
count  10181.000000    10175.000000            9.158000e+03     10181.000000   
mean    1972.745310        5.295725            9.266788e+04        71.391808   
std       32.556683        6.131778            1.439976e+05        25.803497   
min     1900.000000        0.000000            3.636000e+03         1.000000   
25%     1956.000000        3.000000            2.908400e+04        57.000000   
50%     1979.000000        4.000000            4.679700e+04        79.000000   
75%     2000.000000        6.000000            9.392000e+04        92.000000   
max     2019.000000       99.000000            1.926841e+06       100.000000   

       SourceEUIWN(kBtu/sf)  SiteEUIWN(kBtu/sf)  GHGEmissionsIntensity  
count          10123.000000        10122.000000           10181.000000  
mean             116.683345           50.600682               1.086118  
std              243.746922          185.088106               9.284041  
min               -2.100000            0.000000              -0.020000  
25%               72.000000           28.200001               0.200000  
50%               89.900000           37.100000               0.590000  
75%              122.600000           54.900000               1.200000  
max            21839.400000        18097.100000             927.700000

In [ ]:
# Drop Source EUI<0
# Drop GHG emission with < 0
# Drop source EUI > 1000
# Remove number of floors = 99 **
# Remove GFA missing values
# Remove Largest property used type missing values
# Remove SourceEUI missing values
# Remove GHG values above 50

In [ ]:
profile_small = ProfileReport(df_energystar)
profile_small.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Data Cleaning

In [16]:
df_energystar.columns

Index(['YearBuilt', 'NumberofFloors', 'PropertyGFABuilding(s)',
       'LargestPropertyUseType', 'ENERGYSTARScore', 'SourceEUIWN(kBtu/sf)',
       'SiteEUIWN(kBtu/sf)', 'GHGEmissionsIntensity'],
      dtype='object')

In [17]:
df_clean = df_energystar
# Drop Source EUI<0
df_clean = df_clean[df_clean['SourceEUIWN(kBtu/sf)']>0]

# Drop GHG emission with < 0
df_clean = df_clean[df_clean['GHGEmissionsIntensity']>0]

# Drop source EUI > 1000
df_clean = df_clean[df_clean['SourceEUIWN(kBtu/sf)']<1000]
df_clean = df_clean[df_clean['SiteEUIWN(kBtu/sf)']<1000]

# Remove number of floors = 99 **

# Remove GFA missing values
df_clean = df_clean[df_clean['PropertyGFABuilding(s)'].notna()]

# Remove Largest property used type missing values
df_clean = df_clean[df_clean['LargestPropertyUseType'].notna()]

# Remove SourceEUI missing values
df_clean = df_clean[df_clean['SourceEUIWN(kBtu/sf)'].notna()]
df_clean = df_clean[df_clean['SiteEUIWN(kBtu/sf)'].notna()]

# Remove GHG values above 10
df_clean = df_clean[df_clean['GHGEmissionsIntensity']<10]

print(len(df_clean)/len(df_energystar))
# print()

0.8846871623612612


In [18]:
df_clean.head()

YearBuilt  NumberofFloors  PropertyGFABuilding(s) LargestPropertyUseType  \
0     1927.0            12.0                 88434.0                  Hotel   
1     1996.0            11.0                 88502.0                  Hotel   
2     1969.0            41.0                759392.0                  Hotel   
3     1926.0            10.0                 61320.0                  Hotel   
4     1980.0            18.0                113580.0                  Hotel   

   ENERGYSTARScore  SourceEUIWN(kBtu/sf)  SiteEUIWN(kBtu/sf)  \
0             60.0            189.000000           84.300003   
1             61.0            179.399994           97.900002   
2             43.0            244.100006           97.699997   
3             56.0            224.000000          113.300003   
4             75.0            215.600006          118.699997   

   GHGEmissionsIntensity  
0                   2.83  
1                   2.86  
2                   2.19  
3                   4.67  
4                   2.88

### 88% of data remains after cleaning

In [19]:
df_clean.to_csv('/content/drive/MyDrive/05839_Final Project/Data/Final dataset/Individual Building Data/cleaned_dataForML.csv', index=False)

## Data Processing

In [42]:
df_clean = pd.read_csv('/content/drive/MyDrive/05839_Final Project/Data/Final dataset/Individual Building Data/cleaned_dataForML.csv')

In [ ]:
df_clean.head()

### Encoding categorical Largest Property Use Type:

In [ ]:
! pip install transformers

In [ ]:
from transformers import BertTokenizer, BertModel
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained("bert-base-uncased")
text = "Replace me by any text you'd like."
encoded_input = tokenizer(text, return_tensors='pt')
output = model(**encoded_input)

In [ ]:
output.to_tuple()[-1]

In [ ]:
text1 = "Multifamily Housing"
text2 = "Multifamily"
text3 = "Office"

# text = [text1, text2, text3]
encoded_input = tokenizer(text1, return_tensors='pt')
output1 = model(**encoded_input)[-1].detach().numpy()

encoded_input = tokenizer(text2, return_tensors='pt')
output2 = model(**encoded_input)[-1].detach().numpy()

encoded_input = tokenizer(text3, return_tensors='pt')
output3 = model(**encoded_input)[-1].detach().numpy()

In [ ]:
from scipy.spatial.distance import cosine

print(1-cosine(output1, output2))
print(1-cosine(output1, output3))
print(1-cosine(output2, output3))

0.9352229833602905
0.7340902090072632
0.8823019862174988


In [44]:
df_clean['LargestPropertyUseType'].unique()

array(['Hotel', 'Multifamily Housing', 'Courthouse', 'K-12 School',
       'Office', 'Senior Care Community', 'Medical Office',
       'Retail Store', 'Hospital (General Medical & Surgical)',
       'Residence Hall/Dormitory', 'Financial Office',
       'Non-Refrigerated Warehouse', 'Worship Facility', 'Parking',
       'Supermarket/Grocery Store', 'Distribution Center',
       'Wholesale Club/Supercenter', 'Refrigerated Warehouse', 'Other',
       'Bank Branch', 'Multifamily', 'Senior Care', 'Medical Off',
       'Retail Stor', 'Residence H', 'Hospital (G', 'Financial O',
       'Non-Refrige', 'Self-Storag', 'Worship Fac', 'Supermarket',
       'Distributio', 'Manufacturi', 'Wholesale C', 'Refrigerate',
       'Senior Living Community', 'College/University', 'Strip Mall'],
      dtype=object)

In [45]:
df_clean['LargestPropertyUseType'] = df_clean['LargestPropertyUseType'].replace({
    'Multifamily': 'Multifamily',
    'Hospital (G': 'Hospital',
    'Hospital (General Medical & Surgical)': 'Hospital',
    'Senior Care' : 'Senior Care Center',
    'Senior Care Community': 'Senior Care Center',
    'Medical Off': 'Medical Office',
    'Retail Stor': 'Retail Store',
    'Residence H': 'Residence Hall',
    'Residence Hall/Dormitory': 'Residence Hall',
    'Financial O': 'Financial Office',
    'Non-Refrige': 'Non-Refrigerated Warehouse',
    'Self-Storag': 'Self Storage',
    'Worship Fac': 'Worship Facility',
    'Supermarket/Grocery Store': 'Supermarket',
    'Distributio': 'Distribution Center',
    'Manufacturi': 'Manufacturing Center',
    'Wholesale C': 'Wholesale Club/Supercenter',
    'Refrigerate': 'Refrigerated Warehouse',
    'Senior Living Community': 'Senior Care Center',
})

In [46]:
df_clean['LargestPropertyUseType'].unique()

array(['Hotel', 'Multifamily Housing', 'Courthouse', 'K-12 School',
       'Office', 'Senior Care Center', 'Medical Office', 'Retail Store',
       'Hospital', 'Residence Hall', 'Financial Office',
       'Non-Refrigerated Warehouse', 'Worship Facility', 'Parking',
       'Supermarket', 'Distribution Center', 'Wholesale Club/Supercenter',
       'Refrigerated Warehouse', 'Other', 'Bank Branch', 'Multifamily',
       'Self Storage', 'Manufacturing Center', 'College/University',
       'Strip Mall'], dtype=object)

In [47]:
embedding_dict = dict()

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained("bert-base-uncased")
ind_list = list(df_clean['LargestPropertyUseType'].unique())

for t in df_clean['LargestPropertyUseType'].unique():
  encoded_input = tokenizer(t, return_tensors='pt')
  output = model(**encoded_input)[-1].detach().numpy().tolist()[0]
  embedding_dict[t] = np.array(output)
  # embedding_dict[t] = ind_list.index(t)

# embedding_dict

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [48]:
embedding_col = df_clean['LargestPropertyUseType'].apply(lambda x: embedding_dict[x])

df_clean['PropertyTypeEmb'] = embedding_col

In [ ]:
df_clean.head()

In [31]:
df_clean.to_csv('/content/drive/MyDrive/05839_Final Project/Data/Final dataset/Individual Building Data/cleaned_dataForML_withBERT.csv', index=False)

### Test Train Split

In [32]:
df_clean = pd.read_csv('/content/drive/MyDrive/05839_Final Project/Data/Final dataset/Individual Building Data/cleaned_dataForML_withBERT.csv')

In [50]:
df_clean.columns

Index(['YearBuilt', 'NumberofFloors', 'PropertyGFABuilding(s)',
       'LargestPropertyUseType', 'ENERGYSTARScore', 'SourceEUIWN(kBtu/sf)',
       'SiteEUIWN(kBtu/sf)', 'GHGEmissionsIntensity', 'PropertyTypeEmb'],
      dtype='object')

In [ ]:
df_clean.head()

In [52]:
Y = df_clean['ENERGYSTARScore'].to_numpy()
Y

array([60., 61., 43., ..., 97., 74., 98.])

In [ ]:
# df_drop = df_clean.drop(columns=['ENERGYSTARScore', 'LargestPropertyUseType','PropertyTypeEmb'], axis=1)
# r = df_drop.iloc [0].to_numpy()[None,:]
# e = df_clean['PropertyTypeEmb'][0][None,:]
# c = np.c_[r,e]
# c.shape

(1, 773)

In [53]:
# df_drop = df_clean.drop(columns=['ENERGYSTARScore', 'LargestPropertyUseType','SiteEUIWN(kBtu/sf)'], axis=1)
# r = df_drop.to_numpy()
# X = r

In [57]:
from sklearn.preprocessing import normalize
df_drop = df_clean.drop(columns=['ENERGYSTARScore', 'LargestPropertyUseType','PropertyTypeEmb','SiteEUIWN(kBtu/sf)'], axis=1)
r = df_drop.to_numpy()
e = np.array(list(df_clean['PropertyTypeEmb'].to_numpy()))
# print(e[0].shape)
# r = normalize(r)
X = np.c_[r,e]
# X = normalize(X)
# X = e
# print(r.shape, e.shape)
print(X.shape)

(9007, 773)


In [58]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.3, random_state=42)

## Machine Learning Models:

In [59]:
from sklearn.model_selection import cross_val_score

### KNN

In [74]:
from sklearn.neighbors import KNeighborsClassifier
clf = KNeighborsClassifier(n_neighbors=21)
scores = cross_val_score(clf, X_train, y_train, cv=5)
scores

array([0.02854877, 0.02934179, 0.02854877, 0.02934179, 0.03968254])

### KMeans

In [75]:
from sklearn.cluster import KMeans

kmeans = KMeans(n_clusters=5, random_state=0)
scores = cross_val_score(kmeans, X_train, y_train, cv=5)
scores

array([-2.24156732e+12, -1.81202353e+12, -1.64075887e+12, -1.68242609e+12,
       -1.68949947e+12])

### Linear Regression

In [76]:
from sklearn.linear_model import LinearRegression

reg = LinearRegression()
scores = cross_val_score(reg, X_train, y_train, cv=5)
scores

array([0.43935031, 0.41310532, 0.40106632, 0.41045066, 0.40808029])

### SVM

In [77]:
from sklearn.svm import SVR

clf = SVR(C=1.0, epsilon=0.2, degree=5)
scores = cross_val_score(clf, X_train, y_train, cv=5)
scores

array([-0.07456061, -0.06222663, -0.08454039, -0.06339693, -0.06943052])

## DT

In [78]:
from sklearn import tree

clf = tree.DecisionTreeRegressor()
scores = cross_val_score(clf, X_train, y_train, cv=5)
scores

array([0.48082804, 0.40975249, 0.40611401, 0.42836437, 0.44004892])

## Random Forest

In [60]:
from sklearn.ensemble import RandomForestRegressor

clf = RandomForestRegressor(n_estimators=200,max_depth=10, random_state=0)
scores = cross_val_score(clf, X_train, y_train, cv=5)
scores

array([0.70508991, 0.66634162, 0.66105545, 0.67808841, 0.64782509])

## Kernel Ridge

In [80]:
from sklearn.kernel_ridge import KernelRidge

clf = KernelRidge(alpha=1.0)
scores = cross_val_score(clf, X_train, y_train, cv=5)
scores

array([0.44085626, 0.41919134, 0.40305692, 0.41022087, 0.40727586])

## MLP

In [81]:
from sklearn.neural_network import MLPRegressor

clf = MLPRegressor(random_state=1, max_iter=500)
scores = cross_val_score(clf, X_train, y_train, cv=5)
scores

array([-1.81017088e+00, -1.49589146e+03, -8.81313825e-01, -7.26334233e-01,
       -5.46840181e-01])

## Reporting Results:

In [61]:
np.mean(scores)

0.671680097824969

In [63]:
clf.fit(X_train, y_train)
clf.score(X_test, y_test)

0.6861366455174707